In [1]:
# %pip install pickleshare

In [1]:
import os
os.chdir('/Code/ditto_v2')

In [2]:
%pwd

'c:\\Code\\ditto_v2'

In [3]:
import geopandas as gpd
gdf_de = gpd.read_file('.\JupNB\DE_Data\VG250_GEM_WGS84.shp')
gdf_de.head(1)

<>:2: SyntaxWarning: invalid escape sequence '\J'
<>:2: SyntaxWarning: invalid escape sequence '\J'
C:\Users\User\AppData\Local\Temp\ipykernel_24784\3928986815.py:2: SyntaxWarning: invalid escape sequence '\J'
  gdf_de = gpd.read_file('.\JupNB\DE_Data\VG250_GEM_WGS84.shp')


OBJID     BEGINN  ADE  GF  BSG           ARS       AGS  \
0  DEBKGVG200000008 2022-12-20    6   4    1  010010000000  01001000   

        SDV_ARS        GEN    BEZ  ...   NUTS         ARS_0     AGS_0  \
0  010010000000  Flensburg  Stadt  ...  DEF01  010010000000  01001000   

         WSK    EWZ KFL            DLM_ID          EPK EPK_norm  \
0 2008-01-01  92550  56  DEBKGDL20000E5MA  1652.678571      0.0   

                                            geometry  
0  POLYGON ((9.41266 54.82264, 9.41318 54.82124, ...  

[1 rows x 30 columns]

In [169]:
from src.functionality_maps import Defs, paths
import pandas as pd

l_coverage = '20'
# l_stores = ['decathlon','intersport','sport2000','sportxx','karstadt','engelhorn','sportarena','sportcheck','sportsohle]
l_stores = ['decathlon']
l_states = ['Baden-Württemberg']
radius_km = int(l_coverage)
round_dec = 2

print('Filtering stores...')
pdf_stores = pd.read_json(paths.stores, orient='records', lines=True)
pdf_stores = pdf_stores[pdf_stores['store'].isin(l_stores)]
print(f'  After filtering stores... pdf_stores:{pdf_stores.shape[0]}')
pdf_stores = pdf_stores[pdf_stores['GADM_1'].isin(l_states)]
print(f'  After filtering states... pdf_stores:{pdf_stores.shape[0]}\n')


print('Filtering geometry...')
l_bundeslaender = [Defs.dict_bundeslaender_id[x] for x in l_states]
print(f'  gdf_geom:{gdf_de.shape[0]}')
gdf_geom = gdf_de[gdf_de['SN_L'].isin(l_bundeslaender)]
print(f'  After filtering States, gdf_geom:{gdf_geom.shape[0]}')

print('Removing non-serializable columns...')
l_cols_non_serializable = ['WSK','BEGINN']
gdf_geom = gdf_geom.drop(l_cols_non_serializable,axis=1)

print('Computing areas...')
gdf_geom_6993 = gdf_geom.to_crs(epsg=6933)
gdf_geom_6993['KFL_GPD'] = round(gdf_geom_6993.geometry.area / 10**6, 2)
gdf_geom_4326 = gdf_geom.to_crs(epsg=4326)
gdf_geom_6993['lat'] = gdf_geom_4326.geometry.centroid.y
gdf_geom_6993['lon'] = gdf_geom_4326.geometry.centroid.x



Filtering stores...
  After filtering stores... pdf_stores:89
  After filtering states... pdf_stores:14

Filtering geometry...
  gdf_geom:10990
  After filtering States, gdf_geom:1103
Removing non-serializable columns...
Computing areas...


C:\Users\User\AppData\Local\Temp\ipykernel_24784\2987644750.py:33: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_geom_6993['lat'] = gdf_geom_4326.geometry.centroid.y
C:\Users\User\AppData\Local\Temp\ipykernel_24784\2987644750.py:34: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_geom_6993['lon'] = gdf_geom_4326.geometry.centroid.x


In [170]:
import folium
from src.functionality_maps import f_maps
from shapely import geometry

In [171]:
fg_geom = folium.FeatureGroup(name=f'Geometry [{l_states}]')
gjson = f_maps.get_folium_geojson(gdf_geom, 
                                fields=['GEN'],
                                aliases = ['Name'])
gjson.add_to(fg_geom)

In [172]:
import folium
from src.functionality_maps import f_maps
from shapely import geometry

l_center_points = list(zip(pdf_stores['lat'], pdf_stores['lon']))
l_fg = []
num_inside_towns, num_partly_towns = 0, 0
sum_ewz,sum_kfl, sum_area_geom_int = 0, 0, 0
sum_int_kfl, sum_int_ewz, sum_int_geom = 0, 0, 0


# l_fg_point, l_fg_circle, l_fg_merged = []
# l_fg_inside, l_fg_partly = []

fg_point = folium.FeatureGroup(name=f'Center points [{len(l_center_points)}]')
fg_circle = folium.FeatureGroup(name=f'Circles [r={radius_km} Km, Area={round(3.1415 * radius_km**2, 2)} Km2]')
fg_int = folium.FeatureGroup(name=f'Intersections')
fg_inside = folium.FeatureGroup(name=f'Markers - Inside towns')
fg_partly = folium.FeatureGroup(name=f'Markers - Partly towns')
fg_outside = folium.FeatureGroup(name=f'Markers - Outside towns')
fg_overlay = folium.FeatureGroup(name=f'Overlay - Summary inside')

l_gdf_circles = []
l_gdf_merged_circles = []
for i,center_point in enumerate(l_center_points):
    lat = center_point[0]
    lon = center_point[1]

    center_point = geometry.Point(lon, lat)
    gdf_point = gpd.GeoDataFrame(geometry=[center_point], crs=f'EPSG:4326')
    gjson_point = folium.Marker([center_point.y, center_point.x], 
                                icon=folium.Icon(color="red"),
                                tooltip=folium.features.GeoJsonTooltip(fields=['geometry'], values=['coordinates'])
                                )

    gjson_point.add_to(fg_point)
    # l_fg_point.append(fg_point)
    print(f'Processing [{i+1}/{len(l_center_points)}] {center_point}')
    
    ############# CIRCLE PROJECTION IN 4326 ####################
    # Convert the Shapely circle to a geoDataFrame
    poly_circle = f_maps.circle_around_lat_lon_point(lon=lon, lat=lat, radius=1000 * radius_km)
    gdf = gpd.GeoSeries([poly_circle])
    gdf_overlay = gdf.to_frame(name='geometry').set_crs(epsg=4326)
    gdf_circle_6933 = gdf_overlay.to_crs(epsg=6933)
    l_gdf_circles.append(gdf_circle_6933.iloc[0].geometry)

    # Generate the FeatureGroup and add it to the list
    # fg_circle = folium.FeatureGroup(name=f'Circle [lat={lat}, lon ={lon}, r={radius_km} Km]')
    gjson_circle = folium.GeoJson(gdf_overlay, color='red')
    gjson_circle.add_to(fg_circle)
    # l_fg_circle.append(fg_circle)

    ############# INTERSECTION ####################
    gdf_de_int = gpd.sjoin(gdf_geom_4326, gdf_overlay, 
                        how="inner", predicate="intersects") #\
                            # .drop(l_cols_non_serializable, axis=1)
                            # 

    gdf_de_int['KFL_GPD'] = round(gdf_geom_6993.geometry.area / 10**6, 2)
    int_kfl = gdf_de_int.KFL.sum()
    int_ewz =gdf_de_int.EWZ.sum()
    int_geom = round(gdf_de_int.KFL_GPD.sum(), 2)
    sum_int_kfl += int_kfl
    sum_int_ewz += int_ewz
    sum_int_geom += int_geom

    print(f'int_kfl={int_kfl}Km2, int_geom={int_geom}Km2, int_ewz={int_ewz}')

    gjson = f_maps.get_folium_geojson(gdf_de_int, 
                                      fields=['GEN', 'EWZ', 'KFL', 'KFL_GPD'],
                                        aliases = ['Name', 'Population', 'Area_KFL', 'Area_Geom'])
    gjson.add_to(fg_int)

    ############# OVERLAY / individual ####################

    col_perc = 'PERC_int'

    # Set the column used for NORMALIZATION (denominator)
    gdf_geom_6993['area_geom'] = round(gdf_geom_6993['geometry'].area / 10**6, 2)
    # Overlay geometry with polygon  
    gdf_overlay = gpd.overlay(gdf_geom_6993, gdf_circle_6933, how='intersection')

    # Set the column used for NORMALIZATION (numerator)
    gdf_overlay['area'] = round(gdf_overlay['geometry'].area / 10**6, 2)
    gdf_overlay[col_perc] = gdf_overlay['area'] / gdf_overlay['area_geom']
    
    
    d_columns = {
        'area_geom':{'alias' : 'area',        'is_norm': True,  'is_int':False},
        'KFL':     {'alias' : 'area_data',    'is_norm': True,  'is_int':False},
        'EWZ':     {'alias' : 'Population',   'is_norm': True,  'is_int':True}
    }
    
    gdf_overlay = f_maps.overlay_shapes(gdf_circle=gdf_overlay, 
                                        col_perc=col_perc, 
                                        d_columns=d_columns)


    # ################### Distance to point of interest ##########
    gdf = pd.DataFrame(gdf_overlay[['ARS','lat','lon','PERC_int','GEN']])
    gdf = gpd.GeoDataFrame(gdf, crs='epsg:4326', 
                           geometry=[geometry.Point(xy) for xy in zip(gdf['lon'], gdf['lat'])])
    gdf = f_maps.compute_dist_to_lat_lon(gdf, lon=center_point.x, lat=center_point.y, round_dec=2, units='km')

    #######################  Gemeinde Markers  ##########################
    
    gdf_inside = gdf[gdf[col_perc] == 1.0]
    num_inside_towns += gdf_inside.shape[0]
    print(f'Inside ={ gdf_inside.shape[0]}')
    fg_inside_circle = f_maps.get_markers_polygon(gdf_inside, col_perc=col_perc,
                                               l_tooltip=['GEN','dist'], 
                                               name=f'Markers inside {gdf_inside.shape[0]}', color='darkgreen')
    fg_inside_circle.add_to(fg_inside)

    gdf_partly = gdf[gdf[col_perc] != 1.0]
    num_partly_towns += gdf_partly.shape[0]
    fg_partly_circle = f_maps.get_markers_polygon(gdf_partly, col_perc=col_perc,
                                               l_tooltip=['GEN','dist'], 
                                               name=f'Markers partly {gdf_partly.shape[0]}', color='orange')
    fg_partly_circle.add_to(fg_partly)


    # gdf_outside = gdf[gdf[col_perc] != 1.0]
    
    ############# OVERLAY / merged ####################

    l_cols_percentaged = ['area_geom', 'EWZ', 'KFL']
    gdf_merge = f_maps.merge_shapes(gdf_overlay, l_col_percs=l_cols_percentaged,
                                    d_percs={'data':'KFL', 'geom':'area_geom'}, 
                                    num_dec=round_dec, is_logging=True)

    gdf_merge['num_in'] = gdf_inside.shape[0]
    gdf_merge['num_part'] = gdf_partly.shape[0]

    l_gdf_merged_circles.append(gdf_merge)
    
    gjson = f_maps.get_folium_geojson(
        gdf_merge, 
        fields=[
            'perc_data', 
            'KFL_int', 'KFL',
            'perc_geom',
            'area_geom_int', 'area_geom',
            'EWZ_int', 'EWZ',
            'num_in', 'num_part', 
            ],
        aliases = [
            'Percentage data', 
            'Area_data intersection [Km2]', 'Area_data shape [Km2]',
            'Percentage geometry',
            'Area_geom intersection [Km2]', 'Area_geom shape [Km2]',
            'Population intersection', 'Population shape',
            '# Localities inside', 
            '# Localities partially inside',
            ])
    gjson.add_to(fg_overlay)
    sum_ewz += gdf_merge['EWZ_int'].sum()
    sum_kfl += gdf_merge['KFL_int'].sum()
    sum_area_geom_int += gdf_merge['area_geom_int'].sum()
    print(f'area_geom_int= {sum_area_geom_int}\n')

Processing [1/14] POINT (8.449674128073184 49.00488565)


c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:274: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  return type(geom)(zip(*func(*zip(*geom.coords))))
c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:276: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  shell = type(geom.exterior)(zip(*func(*zip(*geom.exterior.coords))))


int_kfl=1483Km2, int_geom=1502.0Km2, int_ewz=951511
Inside =20
area_geom = 1502.0
area_geom_int = 1069.74
EWZ = 951511
EWZ_int = 725528
KFL = 1483
KFL_int = 1055.67
perc_data = 0.71
perc_geom = 0.71
area_geom_int= 1069.74

Processing [2/14] POINT (9.9583729 48.4007813)


c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:274: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  return type(geom)(zip(*func(*zip(*geom.coords))))
c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:276: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  shell = type(geom.exterior)(zip(*func(*zip(*geom.exterior.coords))))


int_kfl=1437Km2, int_geom=1456.93Km2, int_ewz=349624
Inside =22
area_geom = 1456.93
area_geom_int = 941.43
EWZ = 349624
EWZ_int = 271281
KFL = 1437
KFL_int = 926.73
perc_data = 0.64
perc_geom = 0.65
area_geom_int= 2011.17

Processing [3/14] POINT (9.437392619846309 48.7026898)


...

int_kfl=1248Km2, int_geom=1262.37Km2, int_ewz=386640
Inside =18
area_geom = 1262.37
area_geom_int = 796.46
EWZ = 386640
EWZ_int = 215493
KFL = 1248
KFL_int = 786.86
perc_data = 0.63
perc_geom = 0.63
area_geom_int= 12682.61

Processing [13/14] POINT (9.182104646022687 48.791258850000006)
int_kfl=1706Km2, int_geom=1738.85Km2, int_ewz=2044829


c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:274: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  return type(geom)(zip(*func(*zip(*geom.coords))))
c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:276: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  shell = type(geom.exterior)(zip(*func(*zip(*geom.exterior.coords))))


Inside =36
area_geom = 1738.85
area_geom_int = 1258.58
EWZ = 2044829
EWZ_int = 1769334
KFL = 1706
KFL_int = 1232.88
perc_data = 0.72
perc_geom = 0.72
area_geom_int= 13941.19

Processing [14/14] POINT (9.300342163579177 48.8168724)


c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:274: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  return type(geom)(zip(*func(*zip(*geom.coords))))
c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\shapely\ops.py:276: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  shell = type(geom.exterior)(zip(*func(*zip(*geom.exterior.coords))))


int_kfl=1754Km2, int_geom=1792.35Km2, int_ewz=2106052
Inside =44
area_geom = 1792.35
area_geom_int = 1258.6
EWZ = 2106052
EWZ_int = 1700314
KFL = 1754
KFL_int = 1228.58
perc_data = 0.7
perc_geom = 0.7
area_geom_int= 15199.79



In [174]:

fg_inside.layer_name = fg_inside.layer_name + f'[{num_inside_towns}/{gdf_geom.shape[0]}]'
fg_partly.layer_name = fg_partly.layer_name + f'[{num_partly_towns}/{gdf_geom.shape[0]}]'
fg_int.layer_name = fg_int.layer_name + f'[Area={sum_int_kfl}, Area_Geom={round(sum_int_geom,round_dec)}, EWZ={sum_int_ewz} ]'



# area_merged_circ = round(poly_merged_circ.area / 10**6, 3)
fg_overlay.layer_name = fg_overlay.layer_name + f'[Area_geom_int={sum_area_geom_int}, \
                                                    , KFL_int={sum_kfl} \
                                                     EWZ_int={sum_ewz}]'
# fg_circle.layer_name = f'Circles [Radius={radius_km} Km, \
#                                     Area={round(3.1415 * radius_km**2, 2)} Km2]'

In [175]:
geoseries_merged_circ = gpd.GeoSeries(l_gdf_circles)
poly_merged_circ = geoseries_merged_circ.union_all()
# poly_merged_circ

geoseries_all_poly_merged = gpd.GeoSeries([poly_merged_circ])
geoseries_all_poly_merged

gdf_circ_poly_merged = geoseries_all_poly_merged.to_frame(name='geometry').set_crs(epsg=6933)
gdf_circ_poly_merged


# Set the column used for NORMALIZATION (denominator)
gdf_geom_6993['area_geom'] = round(gdf_geom_6993['geometry'].area / 10**6, 2)
# Overlay geometry with polygon  
gdf_overlay_indiv = gpd.overlay(gdf_geom_6993, gdf_circ_poly_merged, how='intersection')

# Set the column used for NORMALIZATION (numerator)
gdf_overlay_indiv['area'] = round(gdf_overlay_indiv['geometry'].area / 10**6, 2)
gdf_overlay_indiv[col_perc] = gdf_overlay_indiv['area'] / gdf_overlay_all['area_geom']


d_columns = {
    'area_geom':{'alias' : 'area',        'is_norm': True,  'is_int':False},
    'KFL':     {'alias' : 'area_data',    'is_norm': True,  'is_int':False},
    'EWZ':     {'alias' : 'Population',   'is_norm': True,  'is_int':True}
}

col_perc = 'PERC_int'
gdf_overlay_all = f_maps.overlay_shapes(gdf_circle=gdf_overlay_indiv, 
                                    col_perc=col_perc, 
                                    d_columns=d_columns)
# }
gdf_overlay_all.shape

IntCastingNaNError: Cannot convert non-finite values (NA or inf) to integer

In [176]:
gdf_overlay_indiv.head(5)

OBJID  ADE  GF  BSG           ARS       AGS       SDV_ARS  \
0  DEBKGVG20000040K    6   4    1  081110000000  08111000  081110000000   
1  DEBKGVG20000040L    6   4    1  081150003003  08115003  081150003003   
2  DEBKGVG20000040M    6   4    1  081150028028  08115028  081150028028   
3  DEBKGVG20000040N    6   4    1  081150029029  08115029  081150029029   
4  DEBKGVG20000040O    6   4    1  081150041041  08115041  081150041041   

         GEN       BEZ  IBZ  ... KFL_GPD        lat       lon area_geom  \
0  Stuttgart     Stadt   60  ...  209.95  48.774577  9.172008    209.95   
1  Böblingen     Stadt   61  ...   38.85  48.681833  9.019747     38.85   
2   Leonberg     Stadt   61  ...   48.93  48.790237  9.007012     48.93   
3   Magstadt  Gemeinde   62  ...   19.18  48.744856  8.979303     19.18   
4  Renningen     Stadt   61  ...   30.93  48.772206  8.924277     30.93   

                                            geometry    area  PERC_int  \
0  POLYGON ((890086.186 5519140.548, 890062.887 5...  209.95  5.095874   
1  POLYGON ((873632.552 5505373.157, 873816.137 5...   38.85  0.118402   
2  POLYGON ((867937.043 5516393.419, 868155.837 5...   48.93  1.361436   
3  POLYGON ((865068.904 5510504.873, 865165.707 5...   19.18  0.465873   
4  POLYGON ((860949.389 5513523.328, 861293.374 5...   30.93  1.194670   

  area_geom_int      KFL_int       EWZ_int  
0   1069.878701  1054.845874  3.225000e+06  
1      4.599910     4.617670  6.092957e+03  
2     66.615050    65.348915  6.740741e+04  
3      8.935448     8.851591  4.560433e+03  
4     36.951136    37.034762  2.221608e+04  

[5 rows x 37 columns]

In [177]:
mask1 = ~gdf_geom_4326['ARS'].isin(gdf_overlay_indiv['ARS'])
gdf_outside = gdf_geom_4326[mask1]


gdf_outside['lat'] = gdf_outside.geometry.centroid.y
gdf_outside['lon'] = gdf_outside.geometry.centroid.x
gdf_outside = gdf_outside.to_crs(epsg=4326)
gdf_outside = gpd.GeoDataFrame(gdf_outside, crs='epsg:4326', 
                        geometry=[geometry.Point(xy) for xy in zip(gdf_outside['lon'], gdf_outside['lat'])])
gdf_outside = pd.DataFrame(gdf_outside[['ARS','lat','lon','GEN','geometry']])

gdf = f_maps.compute_dist_to_lat_lon(gdf_outside, lon=center_point.x, lat=center_point.y, round_dec=2, units='km')

fg_outside = f_maps.get_markers_polygon(gdf_outside, col_perc=col_perc,
                                            l_tooltip=['GEN','dist'], 
                                            name=f'Markers outside [{gdf_outside.shape[0]}/{gdf_geom_4326.shape[0]}]', color='red')

C:\Users\User\AppData\Local\Temp\ipykernel_24784\4021705972.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_outside['lat'] = gdf_outside.geometry.centroid.y
c:\Users\User\AppData\Local\Programs\Python\Python312\Lib\site-packages\geopandas\geodataframe.py:1819: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
C:\Users\User\AppData\Local\Temp\ipykernel_24784\4021705972.py:6: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_outside['lo

In [178]:


############# OVERLAY / merged ####################

l_cols_percentaged = ['area_geom', 'EWZ', 'KFL']
gdf_merge = f_maps.merge_shapes(gdf_overlay_all, l_col_percs=l_cols_percentaged,
                                d_percs={'data':'KFL', 'geom':'area_geom'}, 
                                num_dec=round_dec, is_logging=True)

gdf_merge['num_in'] = gdf_inside.shape[0]
gdf_merge['num_part'] = gdf_partly.shape[0]

l_gdf_merged_circles.append(gdf_merge)



fg_overlay_all = folium.FeatureGroup(name=f'Overlay all [elements={len(l_gdf_circles)},' + \
                                    f'KFL_int={gdf_merge.KFL_int.sum()} km2,' + \
                                    # 'KFL={gdf_merge.KFL.sum()},' + \
                                    f'Area_geom_int={gdf_merge.area_geom_int.sum()} km2,' + \
                                    # 'Area_Geom={gdf_merge.area_geom.sum()},' + \
                                    f'EWZ_int={gdf_merge.EWZ_int.sum()},' 
                                    # 'EWZ={gdf_merge.EWZ.sum()} ]' + \
                                    )
gjson = f_maps.get_folium_geojson(
    gdf_merge, 
    fields=[
        'perc_data', 
        'KFL_int', 'KFL',
        'perc_geom',
        'area_geom_int', 'area_geom',
        'EWZ_int', 'EWZ',
        'num_in', 'num_part', 
        ],
    aliases = [
        'Percentage data', 
        'Area_data intersection [Km2]', 'Area_data shape [Km2]',
        'Percentage geometry',
        'Area_geom intersection [Km2]', 'Area_geom shape [Km2]',
        'Population intersection', 'Population shape',
        '# Localities inside', 
        '# Localities partially inside',
        ])
gjson.add_to(fg_overlay_all)

area_geom = 3730.18
area_geom_int = 2402.48
EWZ = 1824884
EWZ_int = 1639860
KFL = 3692
KFL_int = 2378.43
perc_data = 0.64
perc_geom = 0.64


In [179]:
l_fg = [
    # fg_geom, 
    fg_point, fg_circle, fg_int, 
    fg_overlay, fg_overlay_all, 
      fg_inside,fg_partly,
     fg_outside
    ]

In [180]:
import folium.map


m=folium.Map()
for fg in l_fg:
    fg.add_to(m)
folium.LayerControl(position='topright',collapsed=False).add_to(m)
# m.add_child(folium.LatLngPopup())

m.fit_bounds(m.get_bounds())
m

In [144]:
l_center_points

[(51.0484718, 13.7354617), (51.045427, 13.7359245), (51.3424406, 12.3732372)]